In [ ]:
!pip install git+https://github.com/huggingface/accelerate


  Cloning https://github.com/huggingface/accelerate to /tmp/pip-req-build-jjzy91h2
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/accelerate /tmp/pip-req-build-jjzy91h2
  Resolved https://github.com/huggingface/accelerate to commit e11d3ceff3a49378796cdff5b466586d877d5c60
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for accelerate: filename=accelerate-1.2.0.dev0-py3-none-any.whl size=334925 sha256=fe7e7fe23693551890b431567674db7621ed125f02fa185baf8c2737226c7307
  Stored in directory: /tmp/pip-ephem-wheel-cache-ex33hk33/wheels/f6/c7/9d/1b8a5ca8353d9307733bc719107acb67acdc95063bba749f26
Successfully built accelerate
  Attempting uninstall: accelerate
    Found existing installation: accelerate 1.1.1
    Uninstalling accelerate-1.1.1:
      Successfully uninstalled accelerate-1.1.1


In [ ]:
!pip install -qqqU xformers

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.7/16.7 MB 93.7 MB/s eta 0:00:00


In [ ]:
import os
# Disable all integrations like WandB explicitly using the --report_to flag
os.environ["TRANSFORMERS_NO_LOGGING"] = "true"
os.environ["WANDB_MODE"] = "disabled"

In [ ]:
!pip install -qqq datasets
!pip install -qqq transformers==4.45.2 sentence-transformers==3.1.1

from sentence_transformers import SentenceTransformer, InputExample, losses
from sentence_transformers.evaluation import InformationRetrievalEvaluator
from torch.utils.data import DataLoader
import datasets
from huggingface_hub import login

# Step 1: Log in to Hugging Face Hub
huggingface_token = "token"  # Replace with your token
login(token=huggingface_token)

# Load the pre-trained model
model_id = "dunzhang/stella_en_400M_v5"
model = SentenceTransformer(model_id, trust_remote_code=True)

# Load the dataset
obliqa_dataset = datasets.load_dataset("DrishtiSharma/obliqa")

# Constants
BATCH_SIZE = 10
EPOCHS = 5

# Prepare the training data
train_dataset = obliqa_dataset['train']
corpus = {}
queries = {}
relevant_docs = {}
examples = []

for row in train_dataset:
    query_id = row['QuestionID']
    query = row['Question']
    passages = row['Passages']

    queries[query_id] = query

    for passage in passages:
        passage_id = passage['PassageID']
        corpus[passage_id] = passage['Passage']

        if query_id not in relevant_docs:
            relevant_docs[query_id] = []
        relevant_docs[query_id].append(passage_id)

for query_id, query in queries.items():
    if query_id in relevant_docs and relevant_docs[query_id]:
        passage_id = relevant_docs[query_id][0]
        text = corpus[passage_id]
        examples.append(InputExample(texts=[query, text]))

# DataLoader and loss setup
train_loader = DataLoader(examples, batch_size=BATCH_SIZE, shuffle=True)
loss = losses.MultipleNegativesRankingLoss(model)

# Prepare validation data
val_dataset = obliqa_dataset['validation']
val_corpus = {}
val_queries = {}
val_relevant_docs = {}

for row in val_dataset:
    query_id = row['QuestionID']
    query = row['Question']
    passages = row['Passages']

    val_queries[query_id] = query

    for passage in passages:
        passage_id = passage['PassageID']
        val_corpus[passage_id] = passage['Passage']

        if query_id not in val_relevant_docs:
            val_relevant_docs[query_id] = []
        val_relevant_docs[query_id].append(passage_id)

# Define evaluator
evaluator = InformationRetrievalEvaluator(
    queries=val_queries,
    corpus=val_corpus,
    relevant_docs=val_relevant_docs,
    show_progress_bar=True
)

# Train the model
warmup_steps = int(len(train_loader) * EPOCHS * 0.1)

model.fit(
    train_objectives=[(train_loader, loss)],
    evaluator=evaluator,
    epochs=EPOCHS,
    warmup_steps=warmup_steps,
    output_path="stella_en_400M_v5-obliqa-5-epochs",
    evaluation_steps=200,
    show_progress_bar=True
)

print("Training complete.")




   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 13.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 13.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 11.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 16.9 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.9/9.9 MB 91.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 245.3/245.3 kB 20.2 MB/s eta 0:00:00


/usr/local/lib/python3.10/dist-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/316 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/397 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/170k [00:00<?, ?B/s]

...

Computing widget examples:   0%|          | 0/1 [00:00<?, ?example/s]

Batches:   0%|          | 0/88 [00:00<?, ?it/s]

Corpus Chunks: 100%|██████████| 1/1 [00:42<00:00, 42.03s/it]


Batches:   0%|          | 0/88 [00:00<?, ?it/s]

Corpus Chunks:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
# Push the model to Hugging Face Hub
model_name_on_hub = "stella_en_400M_v5-obliqa-5-epochs"  # Replace with your desired model name
model.push_to_hub(model_name_on_hub)

print(f"Model has been pushed to Hugging Face Hub under the name: {model_name_on_hub}")